<a href="https://colab.research.google.com/github/Termi1878/dw_matrix_road_sign/blob/master/day3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [10]:
import pandas as pd
import numpy as np
import os
import datetime

import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPool2D, Dense, Flatten, Dropout
from tensorflow.keras.utils import to_categorical

%load_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [2]:
cd "/content/drive/My Drive/Colab Notebooks/dw-matrix/matrix_three/dw_matrix_road_sign/"

/content/drive/My Drive/Colab Notebooks/dw-matrix/matrix_three/dw_matrix_road_sign


In [0]:
train = pd.read_pickle('data/train.p')
test = pd.read_pickle('data/test.p')

X_train, y_train = train['features'], train['labels']
X_test, y_test = test['features'], test['labels']

In [4]:
to_categorical(y_train)[0]

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 1., 0.], dtype=float32)

In [0]:
if y_train.ndim == 1: y_train = to_categorical(y_train)
if y_test.ndim == 1: y_test = to_categorical(y_test)

input_shape = X_train.shape[1:]
num_classes = y_train.shape[1]

In [0]:
model = Sequential([
  Conv2D(filters=64, kernel_size=(3, 3), activation="relu", input_shape=input_shape),

  Flatten(),

  Dense(num_classes, activation='softmax'),
])

In [6]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 30, 30, 64)        1792      
_________________________________________________________________
flatten (Flatten)            (None, 57600)             0         
_________________________________________________________________
dense (Dense)                (None, 43)                2476843   
Total params: 2,478,635
Trainable params: 2,478,635
Non-trainable params: 0
_________________________________________________________________


In [7]:
model.compile(loss='categorical_crossentropy', optimizer='Adam', metrics=['accuracy'])
model.fit(X_train,y_train)

1088/1088 [==============================] - 8s 7ms/step - loss: 6.9637 - accuracy: 0.7763


In [0]:
def get_cnn_v1(input_shape, num_classes):
  return Sequential([
  Conv2D(filters=64, kernel_size=(3, 3), activation="relu", input_shape=input_shape),

  Flatten(),

  Dense(num_classes, activation='softmax'),
  ])
def train_model(model,X_train,y_train, params_fit={}):
  model.compile(loss='categorical_crossentropy', optimizer='Adam', metrics=['accuracy'])
  logdir = os.path.join("logs", datetime.datetime.now().strftime("%Y$m$d-$H$M$S"))
  tensorboard_callback = tf.keras.callbacks.TensorBoard(logdir,histogram_freq=1)
  model.fit(
      X_train,
      y_train,
      batch_size=params_fit.get('batch_size',128),
      epochs=params_fit.get('epochs',5),
      verbose=params_fit.get('verbose',1),
      validation_data=params_fit.get('validation_data',(X_train,y_train)),
      callbacks=[tensorboard_callback]
  )
  return logdir

In [15]:
model = get_cnn_v1(input_shape, num_classes)
logdir = train_model(model,X_train,y_train)

Epoch 1/5
272/272 [==============================] - 7s 24ms/step - loss: 38.8863 - accuracy: 0.6980 - val_loss: 0.2967 - val_accuracy: 0.9282
Epoch 2/5
272/272 [==============================] - 6s 24ms/step - loss: 0.2678 - accuracy: 0.9373 - val_loss: 0.1732 - val_accuracy: 0.9591
Epoch 3/5
272/272 [==============================] - 6s 24ms/step - loss: 0.1783 - accuracy: 0.9591 - val_loss: 0.1400 - val_accuracy: 0.9659
Epoch 4/5
272/272 [==============================] - 6s 24ms/step - loss: 0.1407 - accuracy: 0.9688 - val_loss: 0.0953 - val_accuracy: 0.9780
Epoch 5/5
272/272 [==============================] - 6s 24ms/step - loss: 0.0973 - accuracy: 0.9773 - val_loss: 0.1310 - val_accuracy: 0.9701


In [16]:
%tensorboard --logdir logs

<IPython.core.display.Javascript object>

In [0]:
def get_cnn_v2(input_shape, num_classes):
  return Sequential([
   Conv2D(filters=32, kernel_size=(3, 3), activation="relu", input_shape=input_shape),
   MaxPool2D(),
   Dropout(0.5),
   Conv2D(filters=64, kernel_size=(3, 3), activation="relu"),
   MaxPool2D(),
   Dropout(0.3),

   Flatten(),

   Dense(1024, activation='relu'),
   Dropout(0.5),
   Dense(num_classes, activation='softmax'),
  ])

In [20]:
model = get_cnn_v2(input_shape, num_classes)
params_fit={
  'epochs': 25  
}
logdir = train_model(model,X_train,y_train, params_fit)

Epoch 1/25
272/272 [==============================] - 7s 25ms/step - loss: 8.1607 - accuracy: 0.0960 - val_loss: 3.0829 - val_accuracy: 0.1788
Epoch 2/25
272/272 [==============================] - 6s 23ms/step - loss: 2.4599 - accuracy: 0.3217 - val_loss: 1.7855 - val_accuracy: 0.4789
Epoch 3/25
272/272 [==============================] - 6s 23ms/step - loss: 1.5555 - accuracy: 0.5267 - val_loss: 0.8019 - val_accuracy: 0.7835
Epoch 4/25
272/272 [==============================] - 6s 23ms/step - loss: 0.9688 - accuracy: 0.7007 - val_loss: 0.4849 - val_accuracy: 0.8787
Epoch 5/25
272/272 [==============================] - 6s 23ms/step - loss: 0.6751 - accuracy: 0.7899 - val_loss: 0.3048 - val_accuracy: 0.9318
Epoch 6/25
272/272 [==============================] - 6s 23ms/step - loss: 0.5276 - accuracy: 0.8365 - val_loss: 0.1954 - val_accuracy: 0.9591
Epoch 7/25
272/272 [==============================] - 6s 23ms/step - loss: 0.4500 - accuracy: 0.8604 - val_loss: 0.1398 - val_accuracy: 0.9698

In [21]:
%tensorboard --logdir logs

Reusing TensorBoard on port 6006 (pid 626), started 0:14:46 ago. (Use '!kill 626' to kill it.)

<IPython.core.display.Javascript object>